In [10]:
import numpy as np
import plotly.graph_objects as go

def sigmoid(z):
    return 1/(1+np.exp(-z))

# Define positive and negative data points
positive_points = np.array([[2,3],
                           [4,5],
                           [3,6],
                           [5,4]])

negative_points = np.array([[-2,-3],
                           [-4,-5],
                           [-3,-6],
                           [-5,-4]])

# Create a grid of 'x' and 'y' values
x = np.linspace(-10,10,100)
y = np.linspace(-10,10,100)
X,Y = np.meshgrid(x,y)

# Define weights and bias for the 2D Classifier
w1, w2, b = 1, 1, 0  # These can be adjusted as needed

# Compute 'z' as a linear classifier combination of 'x' and 'y'
Z = w1 * X + w2 * Y + b  # Fixed variable name (z to Z)

# Evaluate the sigmoid function 
S = sigmoid(Z)

# Create trace for positive points on the XY-plane
positive_trace = go.Scatter3d(
    x=positive_points[:,0],
    y=positive_points[:,1],
    z=np.zeros(positive_points.shape[0]),  # Fixed z-position
    mode='markers',  # Fixed typo 'markers'
    marker=dict(size=5, color='blue', opacity=0.8),
    name='Positive Points'
)

# Create trace for negative points on the XY-plane
negative_trace = go.Scatter3d(
    x=negative_points[:,0],
    y=negative_points[:,1],
    z=np.zeros(negative_points.shape[0]),  # Fixed z-position
    mode='markers',
    marker=dict(size=5, color='red', opacity=0.8),
    name='Negative Points'
)

# Create trace for the sigmoid surface
sigmoid_surface = go.Surface(
    x=X,
    y=Y,
    z=S,
    opacity=0.6,
    colorscale='Viridis',  # Fixed typo 'Virdis'
    showscale=False,  # Fixed string to boolean
    name='Sigmoid Surface'
)

# Find boundary where S=0.5 (decision boundary)
boundary_contour = go.Contour(
    x=x,
    y=y,
    z=S,
    contours=dict(start=0.5, end=0.5, size=0),
    line=dict(color='green', width=5),
    name='Decision Boundary'
)

# Create figure object
fig = go.Figure(data=[positive_trace, negative_trace, sigmoid_surface])

# Add 2D contour plot for boundary
fig.add_trace(boundary_contour)

# Update layout
fig.update_layout(
    title='Interactive 3D Sigmoid Visualization with Decision Boundary',
    scene=dict(
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Sigmoid(Z)',
        zaxis=dict(nticks=4, range=[0,1]),
        camera=dict(
            up=dict(x=0, y=0, z=1),
            eye=dict(x=2, y=2, z=0.1)
        )
    ),
    width=800,
    height=600
)

# Show plot
fig.show()

In [11]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def sigmoid(z):
    return 1/(1+np.exp(-z))

# Create data points
positive_points = np.array([[2,3], [4,5], [3,6], [5,4]])
negative_points = np.array([[-2,-3], [-4,-5], [-3,-6], [-5,-4]])

# Create grid
x = np.linspace(-10, 10, 50)
y = np.linspace(-10, 10, 50)
X, Y = np.meshgrid(x, y)

# Initial parameters
initial_params = {'w1': 1, 'w2': 1, 'b': 0}

# Create figure with subplots
fig = make_subplots(
    rows=1, cols=2,
    specs=[[{'type': 'surface'}, {'type': 'scatter'}]],
    subplot_titles=('3D Sigmoid Surface', '2D Decision Boundary'),
    horizontal_spacing=0.1
)

# Calculate initial surface
Z = initial_params['w1'] * X + initial_params['w2'] * Y + initial_params['b']
S = sigmoid(Z)

# Add initial traces
fig.add_trace(go.Surface(
    x=X, y=Y, z=S,
    colorscale='Viridis',
    showscale=False,
    opacity=0.7,
    name='Sigmoid Surface'
), row=1, col=1)

fig.add_trace(go.Scatter(
    x=positive_points[:,0],
    y=positive_points[:,1],
    mode='markers',
    marker=dict(color='blue', size=10),
    name='Positive Class'
), row=1, col=2)

fig.add_trace(go.Scatter(
    x=negative_points[:,0],
    y=negative_points[:,1],
    mode='markers',
    marker=dict(color='red', size=10),
    name='Negative Class'
), row=1, col=2)

fig.add_trace(go.Contour(
    x=x, y=y, z=S,
    contours=dict(start=0.5, end=0.5, size=0),
    line=dict(color='green', width=3),
    name='Decision Boundary',
    showscale=False
), row=1, col=2)

# Create slider steps
steps = []
for w1 in np.linspace(0.1, 3, 15):
    step = dict(
        method='update',
        args=[{'z': [sigmoid(w1 * X + initial_params['w2'] * Y + initial_params['b'])]},
              {'z': [sigmoid(w1 * X + initial_params['w2'] * Y + initial_params['b'])]}],
        label=f'w1: {w1:.1f}'
    )
    steps.append(step)

sliders = [dict(
    active=0,
    currentvalue={"prefix": "Weight 1: "},
    pad={"t": 50},
    steps=steps
)]

# Update layout
fig.update_layout(
    title='Interactive Logistic Regression Visualization',
    scene=dict(
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Probability',
        zaxis=dict(range=[0, 1]),
        camera=dict(eye=dict(x=1.5, y=1.5, z=0.8))
    ),
    scene2=dict(xaxis_title='X', yaxis_title='Y'),
    width=1200,
    height=600,
    sliders=sliders,
    updatemenus=[dict(
        type='buttons',
        buttons=[dict(
            label='Play',
            method='animate',
            args=[None, {
                'frame': {'duration': 300, 'redraw': True},
                'fromcurrent': True,
                'mode': 'immediate'
            }]
        )],
        x=0.1,
        y=0,
        xanchor='right',
        yanchor='top'
    )]
)

# Create frames for animation
frames = []
for w1 in np.linspace(0.1, 3, 15):
    Z = w1 * X + initial_params['w2'] * Y + initial_params['b']
    S = sigmoid(Z)
    
    frame = go.Frame(
        data=[go.Surface(z=S), go.Contour(z=S)],
        name=f'w1={w1:.1f}'
    )
    frames.append(frame)

fig.frames = frames

# Add view buttons
fig.update_layout(
    updatemenus=[dict(
        type='dropdown',
        buttons=[
            dict(label='Reset View',
                 method='relayout',
                 args=['scene.camera', dict(eye=dict(x=1.5, y=1.5, z=0.8))]),
            dict(label='Top View',
                 method='relayout',
                 args=['scene.camera', dict(eye=dict(x=0, y=0, z=2.5))]),
            dict(label='Side View',
                 method='relayout',
                 args=['scene.camera', dict(eye=dict(x=2.5, y=0, z=0))])
        ],
        x=0.85,
        y=0.1
    )]
)

# Show the figure
fig.show()